In [5]:
from selenium import webdriver
from selenium.webdriver.chrome.options import Options
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from bs4 import BeautifulSoup
from datetime import datetime
import pandas as pd
import time
import warnings
warnings.filterwarnings('ignore')
import re
from tqdm import tqdm
from selenium.common.exceptions import TimeoutException
import os

error = 0

def fetch_data_from_ad(driver, url):
    try:
        driver.get(url)
        WebDriverWait(driver, 30).until(EC.presence_of_element_located((By.CSS_SELECTOR, 'h1[class="ad__sc-45jt43-0 htAiPK sc-hSdWYo bYQcLm"]')))
        soup = BeautifulSoup(driver.page_source, 'html.parser')
        
        def get_text_by_index(elements, index, default='N/A'):
            return elements[index].text if len(elements) > index else default

        all_spans = soup.find_all('span', {'class': 'ad__sc-1f2ug0x-1 cpGpXB sc-hSdWYo gwYTWo'})
        details = soup.find('span', text=re.compile('Detalhes do imóvel'))
        rooms_elem = soup.find('span', text='Quartos')
        rooms_no = rooms_elem.find_next_sibling('div').a.text if rooms_elem and rooms_elem.find_next_sibling('div') else 'N/A'
        price_text = get_text_by_index(soup.find_all('h2', {'class': 'ad__sc-12l420o-1 haeKsn sc-hSdWYo grMlBs'}), 1).replace('.', '')
        price = int(price_text) if price_text != 'N/A' else None
        
        data = {
            'TITLE': soup.find('h1', {'class': 'ad__sc-45jt43-0 htAiPK sc-hSdWYo bYQcLm'}).text,
            'LINK': url,
            'DATE_SCRAPE': datetime.today().strftime('%Y-%m-%d'),
            'CEP': get_text_by_index(all_spans, 0),
            'CITY': get_text_by_index(all_spans, 1),
            'NEIGHBORHOOD': get_text_by_index(all_spans, 2),
            'CONDO': get_text_by_index(all_spans, 4),
            'TAX': get_text_by_index(all_spans, 5),
            'AREA': get_text_by_index(all_spans, 6),
            'ROOMS_NO': rooms_no,
            'BATH_NO': get_text_by_index(all_spans, 7),
            'PARKING_SPOTS': get_text_by_index(all_spans, 8),
            'APARTMENT_DETAILS': details.find_next_sibling().text if details and details.find_next_sibling() else 'N/A',
            'PRICE': price
        }
        return data

    except TimeoutException:
        print(f"TimeoutException occurred for URL: {url}. Moving on to the next link.")
        global error
        error += 1
        return {}

df_detailed = pd.DataFrame()

start_index = 0
if os.path.exists('dados_detalhados_olx_1.csv'):
    df_existing = pd.read_csv('dados_detalhados_olx_1.csv')
    if not df_existing.empty:
        last_scraped_link = df_existing.iloc[-1]['LINK']
        matched_link_index = df_links[df_links['link'] == last_scraped_link].index
        if not matched_link_index.empty:
            start_index = matched_link_index[0] + 1
        else:
            print("Last scraped link not found in the links file. Starting from the beginning.")

options = Options()
driver = webdriver.Chrome(options=options)

df_links = pd.read_csv('links_unificados_3.csv').iloc[start_index:]
total_links = len(df_links)

for i, row in tqdm(enumerate(df_links.iterrows()), total=total_links, desc="Scraping", position=0, leave=True):
    print(f"Scraping link {start_index + i + 1}/{start_index + total_links}")
    url = row[1]['link']
    region = row[1]['REGION']
    data = fetch_data_from_ad(driver, url)
    
    if not data:
        continue
    
    data['REGION'] = region
    
    # Create a temporary dataframe with the new data
    df_temp = pd.DataFrame([data])
    df_temp = df_temp[['TITLE', 'LINK', 'DATE_SCRAPE', 'CITY', 'CEP', 'NEIGHBORHOOD', 'CONDO', 'TAX', 'AREA', 'ROOMS_NO', 'BATH_NO', 'PARKING_SPOTS', 'APARTMENT_DETAILS', 'PRICE', 'REGION']]
    
    # Append this temporary dataframe to your main dataframe
    df_detailed = df_detailed.append(df_temp, ignore_index=True)
    
    # Write only the new data (df_temp) to the CSV
    df_temp.to_csv('dados_detalhados_olx_3.csv', index=False, mode='a', header=not os.path.exists('dados_detalhados_olx_1.csv'))
    
    time.sleep(3)
    print(df_temp.head())

driver.quit()
print(f"Scraping completed with {error} errors.")


Last scraped link not found in the links file. Starting from the beginning.


Scraping:   0%|                                                                               | 0/5282 [00:00<?, ?it/s]

Scraping link 1/5282


Scraping:   0%|                                                                    | 1/5282 [00:43<63:19:51, 43.17s/it]

                                               TITLE  \
0  Venda Apartamento 3 quartos São Geraldo Belo H...   

                                                LINK DATE_SCRAPE  \
0  https://mg.olx.com.br/belo-horizonte-e-regiao/...  2023-08-06   

             CITY       CEP NEIGHBORHOOD   CONDO     TAX  AREA ROOMS_NO  \
0  Belo Horizonte  31050640  São Geraldo  R$ 550  R$ 135  75m²        3   

  BATH_NO PARKING_SPOTS           APARTMENT_DETAILS   PRICE      REGION  
0       2             2  Academia, Piscina, Varanda  550000  zona_leste  
Scraping link 2/5282


...

Scraping: 100%|█████████████████████████████████████████████████████████████████▉| 5281/5282 [8:42:32<00:04,  4.87s/it]

                                               TITLE  \
0  Apartamento à Venda - Caiçaras, 2 Quartos,  43 m2   

                                                LINK DATE_SCRAPE  \
0  https://mg.olx.com.br/belo-horizonte-e-regiao/...  2023-08-06   

             CITY       CEP NEIGHBORHOOD CONDO   TAX  AREA ROOMS_NO BATH_NO  \
0  Belo Horizonte  30775340     Caiçaras  R$ 0  R$ 0  43m²        2       1   

  PARKING_SPOTS APARTMENT_DETAILS   PRICE         REGION  
0             0               N/A  226000  zona_noroeste  
Scraping link 5282/5282


Scraping: 100%|██████████████████████████████████████████████████████████████████| 5282/5282 [8:42:36<00:00,  5.94s/it]

                                             TITLE  \
0  Apartamento à Venda - Glória, 2 Quartos,  55 m2   

                                                LINK DATE_SCRAPE  \
0  https://mg.olx.com.br/belo-horizonte-e-regiao/...  2023-08-06   

             CITY       CEP NEIGHBORHOOD   CONDO    TAX  AREA ROOMS_NO  \
0  Belo Horizonte  30830440       Glória  R$ 250  R$ 75  55m²        2   

  BATH_NO PARKING_SPOTS APARTMENT_DETAILS   PRICE         REGION  
0       1             1               N/A  190000  zona_noroeste  


Scraping completed with 97 errors.
